In [51]:
from langchain.prompts import PromptTemplate, ChatPromptTemplate, HumanMessagePromptTemplate
from langchain.llms import OpenAI
from langchain.chat_models import ChatOpenAI

from langchain.output_parsers import PydanticOutputParser
from pydantic import BaseModel, Field, validator
from typing import List

In [52]:
model_name = 'text-davinci-003'
temperature = 0.7
model = OpenAI(model_name=model_name, temperature=temperature)

In [53]:
# Define your desired data structure.
class Joke(BaseModel):
    setup: str = Field(description="question to set up a joke")
    punchline: str = Field(description="answer to resolve the joke")
    
    # You can add custom validation logic easily with Pydantic.
    @validator('setup')
    def question_ends_with_question_mark(cls, field):
        if field[-1] != '?' and field[-1] != '？':
            raise ValueError("Badly formed question!")
        return field

In [54]:
# Set up a parser + inject instructions into the prompt template.
parser = PydanticOutputParser(pydantic_object=Joke)

In [55]:
prompt = PromptTemplate(
    template="Answer the user query.\n{format_instructions}\n{query}\n",
    input_variables=["query"],
    partial_variables={"format_instructions": parser.get_format_instructions()}
)

In [56]:
# And a query intented to prompt a language model to populate the data structure.
joke_query = "用中文回答，讲个笑话。"
_input = prompt.format_prompt(query=joke_query)
print("prompt:", _input)

prompt: text='Answer the user query.\nThe output should be formatted as a JSON instance that conforms to the JSON schema below.\n\nAs an example, for the schema {"properties": {"foo": {"title": "Foo", "description": "a list of strings", "type": "array", "items": {"type": "string"}}}, "required": ["foo"]}}\nthe object {"foo": ["bar", "baz"]} is a well-formatted instance of the schema. The object {"properties": {"foo": ["bar", "baz"]}} is not well-formatted.\n\nHere is the output schema:\n```\n{"properties": {"setup": {"title": "Setup", "description": "question to set up a joke", "type": "string"}, "punchline": {"title": "Punchline", "description": "answer to resolve the joke", "type": "string"}}, "required": ["setup", "punchline"]}\n```\n用中文回答，讲个笑话。\n'


In [57]:
output = model(_input.to_string())

In [80]:
for i in range(10):
    output = model(_input.to_string())
    print(i, parser.parse(output))

0 setup='为什么大象不喜欢穿衣服？' punchline='因为衣服太小！'
1 setup='为什么乌龟不能唱歌？' punchline='因为它没有嗓子！'
2 setup='什么东西可以排列成一半？' punchline='一个鸡蛋！'
3 setup='为什么老虎不吃素？' punchline='因为他不能把萝卜拔得出土。'
4 setup='什么植物可以在水里生长？' punchline='水芹菜！'
5 setup='什么可以把一只老虎变成猫？' punchline='把它放进冰箱！'
6 setup='为什么恐龙不能坐飞机？' punchline='因为它没有票！'
7 setup='为什么熊总喜欢去森林游玩？' punchline='因为他想要一个熊朋友！'
8 setup='什么东西可以把一座山搬走？' punchline='风'
9 setup='为什么有些人把面包放进微波炉里？' punchline='因为他们想把它变成“烤面包”。'
